In [1]:
#load generator model
import hydra
import torch
import os
import sys
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))
from hydra import initialize, initialize_config_module, initialize_config_dir, compose
import utils.training_utils as tr_utils


os.environ["CUDA_VISIBLE_DEVICES"] = "1"
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))


#Loading EffectsDiT
config_file_rel="../conf"
config_path="/home/eloi/projects/project_mfm_eloi/src/conf"

config_name="conf_S3_tencymastering_multitrack_paired_stylefxenc2048AF_contentCLAP.yaml"
model_dir="/data5/eloi/checkpoints/S3"
ckpt="1C_tencymastering_vocals-75000.pt"

#config_name="conf_S4_tencymastering_multitrack_paired_stylefxenc2048AF_contentCLAP_CLAPadaptor.yaml"
#model_dir="/data5/eloi/checkpoints/S4"
#ckpt="1C_tencymastering_vocals-100000.pt"

#config_name="conf_S7_tencymastering_multitrack_paired_stylefxenc2048AF_contentCLAP"
#model_dir="/data5/eloi/checkpoints/S7"
#ckpt="1C_tencymastering_vocals-50000.pt"

#config_name="conf_S7_tencymastering_multitrack_paired_stylefxenc2048AF_contentCLAP.yaml"
#model_dir="/data5/eloi/checkpoints/S7"
#ckpt="1C_tencymastering_vocals-50000.pt"

overrides = [
    f"model_dir={model_dir}",
    f"tester.checkpoint={ckpt}",
    "tester.cfg_scale=1.0",
    "tester.sampling_params.T=30",
]

with initialize(version_base=None, config_path=config_file_rel):
    args = compose(config_name=config_name, overrides=overrides)

if not os.path.exists(args.model_dir):
    raise Exception(f"Model directory {args.model_dir} does not exist")

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

diff_params=hydra.utils.instantiate(args.diff_params)

network=hydra.utils.instantiate(args.network)
network=network.to(device)
state_dict = torch.load(os.path.join(args.model_dir,args.tester.checkpoint), map_location=device, weights_only=False)

tr_utils.load_state_dict(state_dict, ema=network)

sampler = hydra.utils.instantiate(args.tester.sampler, network, diff_params, args, )



/home/eloi/myenv/lib/python3.11/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'conf_S3_tencymastering_multitrack_paired_stylefxenc2048AF_contentCLAP.yaml': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)
/home/eloi/myenv/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/eloi/projects/grafx/src/grafx/processors/core/convolution.py:48: UserWarning: FlashFFTConv is not available. Using native convolution instead.
  warnings.warn(
/home/eloi/projects/grafx/src/grafx/processors/core/fft_filterbank.py:144: UserWarning: At least one bark filterbank has all zero values. The value for `n_bins` (49) may be set too high. Or, the value for `num_frequency_bins` (193) may be 

Initializing EDM_Style with args: () {'type': 've_karras', 'cfg_dropout_prob': 0.2, 'sde_hp': {'sigma_data': 0.025, 'sigma_min': 0.0005, 'sigma_max': 5, 'max_sigma': 5, 'rho': 10}, 'CLAP_args': {'ckpt_path': '/data5/eloi/checkpoints/laion_clap/music_audioset_epoch_15_esc_90.14.patched.pt', 'distance_type': 'cosine', 'normalize': True, 'use_adaptor': False, 'adaptor_checkpoint': None, 'adaptor_type': None, 'add_noise': False, 'noise_sigma': 0.1}, 'fx_encoder_plusplus_args': {'distance_type': 'cosine', 'ckpt_path': '/home/eloi/projects/project_mfm_eloi/src/utils/feature_extractors/ckpt/fxenc_plusplus_default.pt'}, 'default_shape': [1, 3, 64, 33]}


/home/eloi/myenv/lib/python3.11/site-packages/timm/models/layers/__init__.py:48: FutureWarning: Importing from timm.models.layers is deprecated, please import via timm.layers
  warnings.warn(f"Importing from {__name__} is deprecated, please import via timm.layers", FutureWarning)
/home/eloi/myenv/lib/python3.11/site-packages/torch/functional.py:554: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at /pytorch/aten/src/ATen/native/TensorShape.cpp:4314.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Load the specified checkpoint /data5/eloi/checkpoints/laion_clap/music_audioset_epoch_15_esc_90.14.patched.pt from users.
Loaded checkpoint from epoch 25
Model loaded successfully on cuda
No module named 'flash_attn'
flash_attn not installed, disabling Flash Attention
Loading state dict
dict_keys(['it', 'network', 'optimizer', 'ema', 'args'])
Attempt 1: trying with strict=True


In [2]:
#Loading blackbox mapper

#config_name="conf_M2_mapper_blackbox_predictive_fxenc2048AFv3CLAP_paired.yaml"
#model_dir="/data5/eloi/checkpoints/M2_mapper_blackbox_TM"
#ckpt="mapper_blackbox_TCN-44000.pt"

config_name="conf_M3_mapper_blackbox_predictive_fxenc2048AFv3CLAP_paired.yaml"
model_dir="/data5/eloi/checkpoints/M3_mapper_blackbox_TM_aug"
ckpt="mapper_blackbox_TCN-50000.pt"

overrides = [
    f"model_dir={model_dir}",
    f"tester.checkpoint={ckpt}",
]

with initialize(version_base=None, config_path=config_file_rel):
    args = compose(config_name=config_name, overrides=overrides)

if not os.path.exists(args.model_dir):
    raise Exception(f"Model directory {args.model_dir} does not exist")

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

mapper=hydra.utils.instantiate(args.network)
mapper=mapper.to(device)
state_dict = torch.load(os.path.join(args.model_dir,args.tester.checkpoint), map_location=device, weights_only=False)

tr_utils.load_state_dict(state_dict, network=mapper)


/home/eloi/myenv/lib/python3.11/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'conf_M3_mapper_blackbox_predictive_fxenc2048AFv3CLAP_paired.yaml': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Load the specified checkpoint /data5/eloi/checkpoints/laion_clap/music_audioset_epoch_15_esc_90.14.patched.pt from users.
Loading state dict
dict_keys(['it', 'network', 'optimizer', 'ema', 'args'])
Attempt 1: trying with strict=True


True

In [2]:
import torch
import os



import torch
from utils.collators import collate_multitrack_paired
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))
from datasets.tency_mastering_multitrack_paired import TencyMastering_Test
import omegaconf

normalize_params=omegaconf.OmegaConf.create(
    {
    "normalize_mode": "rms_dry",
    "rms_dry": -25.0
    }
)

dataset_val= TencyMastering_Test(
  mode= "dry-wet",
  segment_length= 525312,
  fs= 44100,
  stereo= True,
  num_tracks= 5,
  tracks="all",
  path_csv= "/data5/eloi/TencyMastering/PANNs_country_pop/train_split.csv",
  normalize_params=normalize_params,
  num_examples= -1, #use all examples
  RMS_threshold_dB= -40.0,
  seed= 42
)

batch_size = 1
val_loader = torch.utils.data.DataLoader(dataset=dataset_val, batch_size=1, num_workers=1, collate_fn=lambda x: x) 

device=torch.device("cuda" if torch.cuda.is_available() else "cpu")

inputs=[]  # List to store input audio tensors
outputs_ref=[]



-1 num_examples


5it [02:16, 27.38s/it]


test_samples 91 num_examples -1 num_skips 0


In [ ]:
import math
import omegaconf
import torch

Fxencoder_kwargs=omegaconf.OmegaConf.create(
{
        "ckpt_path": "/home/eloi/projects/project_mfm_eloi/src/utils/feature_extractors/ckpt/fxenc_plusplus_default.pt"
}
)

from evaluation.feature_extractors import load_fx_encoder_plusplus_2048
feat_extractor = load_fx_encoder_plusplus_2048(Fxencoder_kwargs, device)

from utils.AF_features_embedding_v2 import AF_fourier_embedding
AFembedding= AF_fourier_embedding(device=device)

def FxEnc(x):
    """
    x: tensor of shape [B, C, L] where B is the batch size, C is the number of channels and L is the length of the audio
    """
    z=feat_extractor(x)
    z= torch.nn.functional.normalize(z, dim=-1, p=2)  # normalize to unit variance
    z= z* math.sqrt(z.shape[-1])  # rescale to keep the same scale

    z_af,_=AFembedding.encode(x)
    z_af=z_af* math.sqrt(z_af.shape[-1])  # rescale to keep the same scale

    z_all= torch.cat([z, z_af], dim=-1)

    #now L2 normalize

    norm_z= z_all/ math.sqrt(z_all.shape[-1])  # normalize by dividing by sqrt(dim) to keep the same scale

    #l2 normalize
    #norm_z=torch.nn.functional.normalize(norm_z, dim=-1, p=2)  # normalize to unit variance

    return norm_z

def embedding_post_processing(z):
    """
    L2 normalize each of the features in z
    """
    z_fxenc=z[..., :2048]  # assuming the FxEncoder features are the first 2048 dimensions
    z_af=z[..., 2048:]  # assuming the AF features are the last 2048 dimensions

    z_fxenc=torch.nn.functional.normalize(z_fxenc, dim=-1, p=2)  # normalize to unit variance
    z_af=torch.nn.functional.normalize(z_af, dim=-1, p=2)

    z_fxenc=z_fxenc * math.sqrt(z_fxenc.shape[-1])  # rescale to keep the same scale
    z_af=z_af * math.sqrt(z_af.shape[-1])  # rescale to

    z_all= torch.cat([z_fxenc, z_af], dim=-1)

    z_all= z_all/ math.sqrt(z_all.shape[-1])  # normalize by dividing by sqrt(dim) to keep the same scale

    #l2 normalize
    #z_all=torch.nn.functional.normalize(z_all, dim=-1, p=2)  # normalize to unit variance
    return z_all


def get_log_rms_from_z(z):

    z = z * math.sqrt(z.shape[-1])  # rescale to keep the same scale
    AF=z[...,2048:]  # assuming the AF features are the last 2048 dimensions
    AF=AF/ math.sqrt(AF.shape[-1])  # normalize to unit variance

    features= AFembedding.decode(AF)
    log_rms=features[0]

    return log_rms


def generate_Fx(x, input_type="dry",num_samples=1, T=30):
    B, N, C, L = x.shape  # B is the batch size, N is the number of tracks, C is the number of channels and L is the length of the audio

    masks= torch.ones((B, N), dtype=torch.bool, device=device)  # Create masks for all tracks, assuming all tracks are present

    shape=sampler.diff_params.default_shape
    shape= [num_samples, N,*shape[2:]]  # B is the batch size, we want to sample B samples

    sampler.T=T

    with torch.no_grad():
        is_wet= "wet" in input_type
        cond, x_preprocessed=sampler.diff_params.transform_forward(x,  is_condition=True, is_test=True, masks=masks, is_wet=is_wet)
        cond=cond.expand(shape[0], -1, -1,-1)  # Expand the condition to match the batch size
        preds, noise_init = sampler.predict_conditional(shape, cond=cond.contiguous(), cfg_scale=args.tester.cfg_scale, device=device,  masks=masks)

    return preds

def apply_rms(y_hat, z_pred):
    """
    Apply RMS normalization to the generated audio y_hat based on the predicted features z_pred.
    """
    pred_logrms=get_log_rms_from_z(z_pred)  # get the log RMS from the generated features
    rms_y=10**(pred_logrms.unsqueeze(-1)/20)  # Convert log RMS to linear scale

    gain= (rms_y / torch.sqrt(torch.mean(y_hat**2, dim=(-1), keepdim=True) + 1e-6))  # Calculate the gain factor
    y_final= y_hat *gain  # Apply the gain factor to the generated audio 
    return y_final

from utils.data_utils import apply_RMS_normalization

def apply_effects(x, z_pred):

    x_norm= x[0].mean(dim=1, keepdim=True)  # Normalize the input audio by its mean across the tracks
    x_norm=apply_RMS_normalization(x_norm,-25.0, device=device)

    with torch.no_grad():
        y_hat=mapper(x_norm, z_pred)
    
    y_final=apply_rms(y_hat, z_pred)  # Apply RMS normalization to the generated audio

    return y_final
        

Loaded checkpoint from epoch 25
Model loaded successfully on cuda


In [21]:

from tqdm import tqdm
from fx_model.fx_pipeline import DiffVoxFxMultitrack, DiffVoxFxMaster

loss_fn = lambda x, y: (1-torch.cosine_similarity(x, y, dim=-1)).sum()

def apply_effects_ITO(x, z_pred,  lr=0.1, num_iterations=100):

    N, C, L = x.shape  # N is the number of tracks, C is the number of channels and L is the length of the audio

    fx=DiffVoxFxMultitrack(sample_rate=44100, device=device, N_tracks=x.shape[0]).to(device)

    optimizer = torch.optim.Adam(fx.parameters(), lr=lr)    

    x_norm= x.mean(dim=1, keepdim=True)  # Normalize the input audio across the tracks
    x_norm=apply_RMS_normalization(x_norm,-25.0, device=device)

    #anneal the learning rate depending on the number of iterations
    #scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10, eta_min=0)
    #scheduler = torch.optim.lr_scheduler.CosineAnnealingWarmRestarts(
    #    optimizer, 
    #    T_0=50,           # Initial restart interval
    #    T_mult=1,         # Keep same cycle length
    #    eta_min=1e-6      # Don't go completely to zero
    ##)

    scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
        optimizer, 
        mode='min', 
        factor=0.5, 
        patience=10,
        min_lr=1e-5
    )

    with tqdm(range(num_iterations), disable=False) as pbar:
        for i in pbar:
            y_hat=fx(x_norm)

            pred_features=FxEnc(y_hat)  # Get the features from the generated audio

            loss=loss_fn(pred_features, z_pred)  # Compute the loss between the predicted features and the target features

            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            scheduler.step(loss)

            postfix_dict = {
                "loss": loss.item(),
                "lr": scheduler.get_last_lr()[0] 
            }
    
            pbar.set_postfix(
                **postfix_dict,
            )

    y_hat=apply_rms(y_hat, z_pred)  # Apply RMS normalization to the generated audio

    y_final=y_hat
    return y_final

In [ ]:

#import soundfile as sf
#import matplotlib.pyplot as plt
from sklearn.manifold import TSNE   
from utils.log import make_PCA_figure

#for i in range(1):
i=1
datav=dataset_val[i],
collated_data= collate_multitrack_paired(datav)
x=collated_data['x'].to(device)  # x is a tensor of shape [B, N, C, L] where B is the batch size, N is the number of tracks, C is the number of channels and L is the length of the audio
y=collated_data['y'].to(device)  # y is a tensor of shape [B, N, C, L] where B is the batch size, N is the number of tracks, C is the number of channels and L is the length of the audio

z_ref=FxEnc(y[0])  # z_y is a tensor of shape [B, N, D] where D is the dimension of the features (2048 + 2048 = 4096)

taxonomy=collated_data['taxonomies']  # taxonomy is a list of lists of taxonomies, each list is a track, each taxonomy is a string of 2 digits

mixture=y.sum(dim=1, keepdim=False)


from IPython.display import Audio, display
print("reference")
a=Audio(mixture[0].cpu().clamp(-1,1), rate=44100, normalize=False)  # Play the first track of the input audio
display(a)  # Display the audio player in the notebook


y_final=apply_effects_ITO(x[0], z_ref.detach(), num_iterations=500)  # Apply the effects to the input audio
y_hat_mixture=y_final.sum(dim=0, keepdim=False)
a=Audio(y_hat_mixture.detach().cpu().clamp(-1,1), rate=44100, normalize=False)  # Play the first track of the generated audio
display(a)


#preds=generate_Fx(x, input_type="dry", num_samples=200, T=30) 
#preds=embedding_post_processing(preds)  # post-process the generated features
#
# Step 1: Optional PCA preprocessing (recommended for high dimensions)
## If you want to add PCA preprocessing:
#from sklearn.decomposition import PCA
#pca = PCA(n_components=100)
#combined_data_flat = torch.cat([preds.view(preds.shape[0],-1), z_ref.view(-1).unsqueeze(0)], dim=0).cpu().numpy()
#combined_data = pca.fit_transform(combined_data_flat)

#tsne =TSNE(n_components=2, perplexity=30)
##combined_data = torch.cat([preds.view(preds.shape[0],-1), z_ref.view(-1).unsqueeze(0)], dim=0).cpu().numpy()
#combined_result = tsne.fit_transform(combined_data)
#
#data_dict = {
#   "predicted": combined_result[:-1],
#   "reference": combined_result[-1:]
#     } 
#
#fig = make_PCA_figure(data_dict, title="TSNE")
#fig.show()


#preds=generate_Fx(x, input_type="dry", num_samples=5) 
#z_pred=preds
#z_pred=preds
#z_pred=embedding_post_processing(preds)  # post-process the generated features



#print("predictions")
#for j in range(z_pred.shape[0]):
#    y_final=apply_effects_ITO(x[0].detach(), z_pred[j].detach())  # Apply the effects to the input audio
#    y_hat_mixture=y_final.sum(dim=0, keepdim=False)
#    a=Audio(y_hat_mixture.detach().cpu().clamp(-1,1), rate=44100, normalize=False)  # Play the first track of the generated audio
#    display(a)  # Display the audio player in the notebook
#


reference


  1%|          | 5/500 [00:01<02:42,  3.05it/s, loss=0.634, lr=0.1]

 35%|███▌      | 176/500 [01:12<02:20,  2.30it/s, loss=0.0336, lr=0.1]

In [13]:

preds=generate_Fx(x, input_type="dry", num_samples=5) 
z_pred=embedding_post_processing(preds)  # post-process the generated features

print("predictions")
for j in range(z_pred.shape[0]):
    y_final=apply_effects_ITO(x[0], z_pred[j], num_iterations=500)  # Apply the effects to the input audio
    y_hat_mixture=y_final.sum(dim=0, keepdim=False)
    a=Audio(y_hat_mixture.detach().cpu().clamp(-1,1), rate=44100, normalize=False)  # Play the first track of the generated audio
    display(a)  # Display the audio player in the notebook



cfg_scale 1.0


  0%|          | 0/29 [00:00<?, ?it/s]

100%|██████████| 29/29 [00:00<00:00, 34.81it/s]


predictions


100%|██████████| 500/500 [03:19<00:00,  2.50it/s, loss=0.0664, lr=0.025]


 49%|████▉     | 246/500 [01:43<01:46,  2.38it/s, loss=0.0709, lr=0.05]


KeyboardInterrupt: 

In [44]:
print(preds[0].std(), z_ref.std())

tensor(0.0184, device='cuda:0') tensor(0.0184, device='cuda:0')


In [23]:

a=Audio(y_hat_mixture.detach().cpu().clamp(-1,1), rate=44100, normalize=False)  # Play the first track of the generated audio
#sf.write("ref_blackbox_{i}.wav", y_hat_mixture.cpu().clamp(-1,1).numpy(), 44100, subtype='PCM_16')  # Save the generated audio
display(a)

cfg_scale 1.0


100%|██████████| 29/29 [01:32<00:00,  3.21s/it]
